# Phase 1. Road segment clustering

In [1]:
from clustering import *
from load_data import *

BASE_PATH = '/home/ubuntu/EdgeNetData/traffic_inrix'
CORES = cpu_count()
np.random.seed(42)
inrix_map = load_map_inrix()

## Step 1. Sample segments

Randomly select 1 day and 100 road segments over the whole TN area.

In [3]:
Y, M, D = 2019, 6, 1
init_segments=100
nDays=1
metric='dtw'
method='OPTICS'

In [4]:
segment_parquets = glob.glob('%s/year=%d/**' % (BASE_PATH, Y))
seg_cluster_labels = np.zeros(len(segment_parquets))
sample_index = np.random.randint(0, len(segment_parquets), init_segments)
random_segment_parquets = np.take(segment_parquets, sample_index)
print('NO. Segments:', len(segment_parquets))

NO. Segments: 4217


In [5]:
# Data visulization
df = pd.read_parquet(segment_parquets[0], engine='fastparquet')
print('No. records: %d' % df.shape[0])
df.head(3)

No. records: 104832


xd_id measurement_tstamp_str  speed  average_speed  \
index                                                                          
2019-01-01 00:00:00  1363474700    2019-01-01 00:00:00  61.39           61.0   
2019-01-01 00:05:00  1363474700    2019-01-01 00:05:00  61.00           61.0   
2019-01-01 00:10:00  1363474700    2019-01-01 00:10:00  61.00           61.0   

                     reference_speed  travel_time_seconds  confidence_score  \
index                                                                         
2019-01-01 00:00:00             64.0                37.02              22.0   
2019-01-01 00:05:00             64.0                37.26              20.0   
2019-01-01 00:10:00             64.0                37.26              20.0   

                     cvalue  extreme_congestion  regular_congestion  
index                                                                
2019-01-01 00:00:00  100.00            0.006094           -0.040781  
2019-01-01 00:05:00    None            0.000000           -0.046875  
2019-01-01 00:10:00    None            0.000000           -0.046875

In [8]:
from branca.element import Figure
sel_seg = [s.split('/')[-1] for s in random_segment_parquets]
sel_seg = inrix_map[inrix_map['XDSegID'].isin(sel_seg)]
fig = Figure(height=300, width=800)
fmap = folium.Map(location = [36,-86], zoom_start=8)
folium.GeoJson(sel_seg,
            name='Inrix',
            tooltip=folium.features.GeoJsonTooltip(fields=['XDSegID', 'PreviousXD', 'NextXDSegI', 'County'], localize=True),
            style_function=lambda seg: {'color':  '#000000', "weight": 5}).add_to(fmap)
fmap.save('images/cluster_init_samples.html')
fig.add_child(fmap)

## Step 2. Generate initial clusters

- a. compute DTW matrix to measure similarities between samples road segments
- b. generate initial cluster using the DTW matrix.

Dynamic Time Warping (DTW) distance: a commonused metrics for assessing similarity between two temporal sequences. 

DTW distance is calculated as the squared root of the sum of squared distances between every element in $x_i$ and its nearest point in $x_j$.

In [82]:
inrix_mts = sample_inrix_mts(Y, M, D, random_segment_parquets, nDays)
print('Sampled Inrix MTS Shape:', inrix_mts.shape)

Sampled Inrix MTS Shape: (100, 288, 1)


In [129]:
# compute pairwise DTW Distance
distance_matrix = compute_dtw(inrix_mts)
clf = OPTICS(min_samples=5, n_jobs=-1).fit(distance_matrix)
labels = clf.labels_

In [129]:
print('Initial clustering done')
seg_cluster_labels[sample_index] = labels
initial_clusters = {}
for c in np.unique(labels):
    initial_clusters.update({str(c): np.mean(inrix_mts[np.where(labels==c)[0]], axis=0)})

Initial clustering done


In [135]:
temp = initial_clusters.copy()
for k in temp.keys():
    temp[k] = temp[k].ravel()
clstr = pd.DataFrame(temp)
plt.plot(clstr)
plt.title('Mean extreme congestion rate for each cluster (1 day)')
plt.show()

## Step 3. Iteratively merge other segments into initial clusters

Compute DTW distance between remaining road segments and centroids of existing clusters. Then merge them into the nearst one.

In [ ]:
print('Merging other segments...')
osg_index = np.delete(np.arange(len(segment_parquets)), sample_index)

# Speed-up the merging process
osg_index_group = np.array_split(osg_index, CORES)
osg_parquet_groups = [np.take(segment_parquets, x) for x in osg_index_group]
osg_groups_args = list(zip(osg_parquet_groups, [(Y, M, D, 1)]*CORES, [initial_clusters]*CORES, [metric]*CORES))
with ThreadPoolExecutor(max_workers=CORES) as pool:
    results = pool.map(merge_cluster, osg_groups_args)
results = list(results)
for i in range(CORES):
    np.put(seg_cluster_labels, osg_index_group[i], results[i])
    
label_df = pd.DataFrame([])
label_df['label'] = seg_cluster_labels
label_df['xdsegid'] = [int(x.split('/')[-1].split('.')[0]) for x in segment_parquets]
label_df.to_csv('%s/clusters/year=%d/%s/labels.csv' % (BASE_PATH, Y, method), index=None)

In [12]:
inrix_map = generate_cluster_map(Y, method='OPTICS')

label_df = pd.read_csv('%s/clusters/year=%d/%s/labels.csv' % (BASE_PATH, Y, method))
label_df.set_index('xdsegid', inplace=True)
label_df.sort_index(inplace=True)

all_colors = pd.read_csv('colors.csv', header=None).to_numpy().squeeze()
all_colors = np.array_split(all_colors, label_df['label'].unique().shape[0])
    
fig = Figure(height=500)
fmap = folium.Map(location = [36,-86], zoom_start=8)
folium.GeoJson(inrix_map,
            name='Inrix',
            tooltip=folium.features.GeoJsonTooltip(fields=['XDSegID', 'PreviousXD', 'NextXDSegI', 'County'], localize=True),
            style_function=lambda seg: {'color':  all_colors[seg['properties']['label']][0], "weight": 5}).add_to(fmap)
fmap.save('images/clusters.html')
fig.add_child(fmap)